In [1]:
'''
Created on 6 de abr de 2019

@author: pablo-moreira
'''
import json
import os

from ia_utils.bag_of_words import BagOfWordsConfiguracao, \
    BagOfWordsTipoFrequencia, BagOfWords
from ia_utils.dataset_classificador import DatasetClassificador
from ia_utils.normalizador_texto import NormalizadorTexto, \
    NormalizadorTextoConfiguracao
from ia_utils.vocabulario import VocabularioConfiguracao, Vocabulario
from keras.layers.core import Dense, Dropout
from keras.models import Sequential
from keras.models import model_from_json
from typing import Callable

import numpy as np
from sinapses_cliente.modelo.binario import Binario
from sinapses_cliente.modelo.modelo_versao_recurso import ModeloVersaoRecurso
from sinapses_cliente.modelo.requisicao.mensagem import Mensagem
from sinapses_cliente.modelo.requisicao.requisicao_classificacao import RequisicaoClassificacao
from sinapses_cliente.modelo.resposta.classificacao_classe import ClassificacaoClasse
from sinapses_cliente.modelo.resposta.classificacao_classe_conviccao import ClassificacaoClasseConviccao
from sinapses_cliente.modelo.resposta.resposta_classificacao import RespostaClassificacao
from sinapses_cliente.modelo.servico_contexto import ServicoContexto
from sinapses_cliente.modelo.tipo_conteudo import TipoConteudo
from sinapses_cliente.modelo.treinamento_resultado import TreinamentoResultado
from sinapses_cliente.sinapses_pipeline import SinapsesPipeline
from sinapses_cliente.sinapses_sessao import SinapsesSessao
from ia_utils import vocabulario_utils, classificacao_utils

Using TensorFlow backend.


In [2]:
pipeline = SinapsesPipeline.instancia();

def get_normalizador_texto() -> NormalizadorTexto:
    return NormalizadorTexto(NormalizadorTextoConfiguracao(
        substitue_tab_por_espaco = True,
        remove_retorno_carro = True,
        remove_espacos_duplos = True,
        converte_para_minusculo = True,
        extrair_generalizacao = True,
        extrair_extenso_numeral = True
    ))

In [3]:
def encodar_textos(textos: list, classes: list):
    
    quant = 10
    x = []
    y = []
    
    for i in range(len(textos)):
        
        tokens = vocabulario_utils.texto_tokenize(textos[i])
               
        for j in range(len(tokens) - quant):
            x.append(' '.join(tokens[j:j + quant]))
            y.append(classes[i])
        
    return x, y 

In [4]:
def funcao_treinamento(sessao: SinapsesSessao) -> TreinamentoResultado:
    
    modelo_versao = sessao.get_modelo_versao()

    classes = json.loads(modelo_versao.get_recurso_por_nome('classificadorClasses.json').conteudo.bytes)
    
    id2classe = { idx: tupla[0] for idx, tupla in enumerate(classes.items()) }
    classe2id = { v: k for k,v in id2classe.items() }

    diretorio_trabalho = sessao.get_diretorio_trabalho()
    arquivos = []

    for versao_recurso in modelo_versao.get_recursos_por_tipo_recurso('DATASET_TREINAMENTO'):
        arquivo = os.path.join(diretorio_trabalho, versao_recurso.nome)
        versao_recurso.conteudo.salvar_em(arquivo)
        arquivos.append(arquivo)
        
    normalizador_texto = get_normalizador_texto()
    
    dataset = DatasetClassificador(arquivos, diretorio_trabalho, conversor_texto=normalizador_texto.normalizar_texto)
    dataset.carregar_dataset()

    vocabulario_config = VocabularioConfiguracao(
        usar_stemmer = False,
        remover_stopwords= True,
        remover_intersecao= True,
        remover_pontuacao= True,
        percentual_frequencia_min_intersecao= 0.85,
        tamanho_vocabulario= 1000
    )
    
    treino_textos = dataset.get_treino_textos()
    validacao_textos = dataset.get_validacao_textos()
    
    textos = list(treino_textos)
    textos.extend(validacao_textos)
    
    classes = list(dataset.treino_classe)
    classes.extend(dataset.validacao_classe)
    
    vocabulario = Vocabulario(
        textos,
        classes,
        vocabulario_config
    )

    vocabulario_arquivo = diretorio_trabalho + '/vocabulario'
    
    vocabulario.salvar(vocabulario_arquivo)

    bow_configs = BagOfWordsConfiguracao(
        tipo_frequencia=BagOfWordsTipoFrequencia.BINARIA,
        configuracao_superior=vocabulario_config
    )

    bag_of_words = BagOfWords(vocabulario, bow_configs)
            
    treino_x, treino_y = encodar_textos(textos, classes)
    validacao_x, validacao_y = encodar_textos(validacao_textos, dataset.validacao_classe)

    treino_x = np.array(bag_of_words.docs2bow(treino_x))        
    validacao_x = np.array(bag_of_words.docs2bow(validacao_x))
    
    def criar_saida(classes):    
    
        saida = []
        
        for classe in classes:
            
            item = np.zeros(8)
            item[classe2id[classe]] = 1
            
            saida.append(item)
            
        return np.array(saida)
         
    treino_y = criar_saida(treino_y)
    validacao_y = criar_saida(validacao_y)
    
    modelo = Sequential()
    modelo.add(Dense(2000, activation='relu', input_dim=len(treino_x[0])))
    modelo.add(Dropout(0.8))
    modelo.add(Dense(8, activation='sigmoid'))
    modelo.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

    epochs = 10 if sessao.is_desenvolvimento() else 30 

    print('Treinando')
    modelo.fit(treino_x, treino_y, validation_data=(validacao_x, validacao_y), epochs=epochs, batch_size=150)
    
    print('Validando')
    scores = modelo.evaluate(validacao_x, validacao_y)

    modelo_json = modelo.to_json()
    modelo.save_weights(diretorio_trabalho + '/modelo.pesos.h5');
            
    return TreinamentoResultado(scores[1], [
        ModeloVersaoRecurso('vocabulario.csv', Binario.from_arquivo(vocabulario_arquivo + '.csv'), TipoConteudo.TEXT_CSV, 'modelo-treinado'),
        ModeloVersaoRecurso('vocabulario.cfg.json', Binario.from_arquivo(vocabulario_arquivo + '.cfg.json'), TipoConteudo.APPLICATION_JSON, 'modelo-treinado'),
        ModeloVersaoRecurso('id2classe.json', Binario(json.dumps(id2classe)), TipoConteudo.APPLICATION_JSON, 'modelo-treinado'),
        ModeloVersaoRecurso('modelo.json', Binario(bytes(modelo_json, 'UTF-8')), TipoConteudo.APPLICATION_JSON, 'MODELO_TREINADO'),
        ModeloVersaoRecurso('modelo.pesos.h5', Binario.from_arquivo(diretorio_trabalho + '/modelo.pesos.h5'), TipoConteudo.APPLICATION_OCTET_STREAM, 'MODELO_TREINADO')]
    )

In [5]:
def funcao_inicializacao_servico(sessao: SinapsesSessao):

    modelo_versao = sessao.get_modelo_versao()

    normalizador_texto = get_normalizador_texto()
    classes = json.loads(modelo_versao.get_recurso_por_nome('classificadorClasses.json').conteudo.bytes)
    id2classe = json.loads(modelo_versao.get_recurso_por_nome('id2classe.json').conteudo.bytes)
    vocabulario = Vocabulario.carregar_por_bytes(modelo_versao.get_recurso_por_nome('vocabulario.cfg.json').conteudo.bytes,  modelo_versao.get_recurso_por_nome('vocabulario.csv').conteudo.bytes)

    bag_of_words = BagOfWords(vocabulario, BagOfWordsConfiguracao(
        tipo_frequencia=BagOfWordsTipoFrequencia.QUANTIDADE_NO_TEXTO,
        configuracao_superior=vocabulario.configuracao
    ))
        
    modelo = model_from_json(modelo_versao.get_recurso_por_nome('modelo.json').conteudo.bytes)
    
    arquivo_modelo_weights = sessao.get_diretorio_trabalho() + '/modelo_weights.h5'    
    
    modelo_versao.get_recurso_por_nome('modelo.pesos.h5').conteudo.salvar_em(arquivo_modelo_weights)
        
    modelo.load_weights(arquivo_modelo_weights)
       
    return ServicoContexto(
        modelo = modelo,
        classes = classes,
        id2classe = id2classe,
        normalizador_texto = normalizador_texto,
        bag_of_words = bag_of_words
    )

In [6]:
def funcao_servico(sessao: SinapsesSessao, ctx: ServicoContexto, requisicao: RequisicaoClassificacao) -> RespostaClassificacao:    
    
    texto = sessao.get_mensagem_texto(requisicao.mensagem)

    texto = ctx.normalizador_texto.normalizar_texto(texto)

    tokens = vocabulario_utils.texto_tokenize(texto)
    
    texto = tokens[0:min(len(tokens),10)] 

    bow_x = ctx.bag_of_words.doc2bow(texto)

    predicao = ctx.modelo.predict(np.array([bow_x]))[0]

    scores, top_n = classificacao_utils.get_scores_com_top_n(predicao, requisicao.quantidade_classes)

    percentual_max = float(0.0)

    # calcula o valor máximo de percentual relativo
    for item in top_n:
        percentual_max += scores[item]

    resultados = []

    for i in top_n:
        
        codigo = ctx.id2classe[str(i)]
        descricao = ctx.classes[codigo]
        conviccao = float(scores[i] * 100) / percentual_max  # calcula o percentual relativo do item

        resultados.append(ClassificacaoClasseConviccao(ClassificacaoClasse(codigo, descricao), conviccao))

    return RespostaClassificacao(resultados[0].classe, resultados=resultados)

In [7]:
def funcao_teste_servico(_s: SinapsesSessao, _c: ServicoContexto, servico: Callable[[dict], dict]) -> None:
    
    r1 = servico({ 'mensagem': Mensagem.texto('Amazona').to_dict(), 'quantidadeClasses': 2 })
    r2 = servico({ 'mensagem': Mensagem.texto('Stark').to_dict(), 'quantidadeClasses': 2 })
    r3 = servico({ 'mensagem': Mensagem.texto('capitão').to_dict(), 'quantidadeClasses': 2 })
    r4 = servico({ 'mensagem': Mensagem.texto('clark').to_dict(), 'quantidadeClasses': 2 })
    r5 = servico({ 'mensagem': Mensagem.texto('bruce').to_dict(), 'quantidadeClasses': 2 })
    r6 = servico({ 'mensagem': Mensagem.texto('Amazona').to_dict(), 'quantidadeClasses': 2 })
    
    assert r1 == r6

In [8]:
pipeline.definir_treinamento(funcao_treinamento)
pipeline.definir_inicializacao_servico(funcao_inicializacao_servico)
pipeline.definir_servico(funcao_servico)
pipeline.definir_teste_servico(funcao_teste_servico)

In [9]:
#pipeline.executar_teste()

2019-08-27 18:20:10,523 - ia_utils.vocabulario_utils - INFO - Criando os vocabulários por classe...
2019-08-27 18:20:10,567 - ia_utils.vocabulario_utils - INFO - Quantidade de tokens presentes nos vocabularios de todas as classes: 1
2019-08-27 18:20:10,568 - ia_utils.vocabulario_utils - INFO - Quantidade de tokens presentes nos vocabularios de todas as classes com a frequencia minima requerida: 1
2019-08-27 18:20:10,568 - ia_utils.vocabulario_utils - INFO - Exemplos de tokens da interseção:
2019-08-27 18:20:10,568 - ia_utils.vocabulario_utils - INFO - ['comics']
2019-08-27 18:20:10,569 - ia_utils.vocabulario_utils - INFO - Quantidade de items no vocabulario: inicial: 712
2019-08-27 18:20:10,569 - ia_utils.vocabulario_utils - INFO - Quantidade de items no vocabulario: excluindo interseção: 711
2019-08-27 18:20:10,569 - ia_utils.vocabulario_utils - INFO - Quantidade de items no vocabulario: excluindo menos comuns: 711


Treinando
Train on 2080 samples, validate on 2080 samples
Epoch 1/10
2080/2080 [==============================] - 0s 216us/step - loss: 1.9635 - acc: 0.3817 - val_loss: 1.7942 - val_acc: 0.6024
Epoch 2/10
2080/2080 [==============================] - 0s 170us/step - loss: 1.6510 - acc: 0.6490 - val_loss: 1.4405 - val_acc: 0.7490
Epoch 3/10
2080/2080 [==============================] - 0s 162us/step - loss: 1.2079 - acc: 0.8221 - val_loss: 0.8468 - val_acc: 0.9471
Epoch 4/10
2080/2080 [==============================] - 0s 187us/step - loss: 0.5626 - acc: 0.9769 - val_loss: 0.2524 - val_acc: 0.9981
Epoch 5/10
2080/2080 [==============================] - 0s 197us/step - loss: 0.1645 - acc: 0.9976 - val_loss: 0.0708 - val_acc: 0.9995
Epoch 6/10
2080/2080 [==============================] - 0s 178us/step - loss: 0.0576 - acc: 1.0000 - val_loss: 0.0294 - val_acc: 0.9995
Epoch 7/10
2080/2080 [==============================] - 0s 184us/step - loss: 0.0310 - acc: 0.9995 - val_loss: 0.0171 - val_ac